In [ ]:
!pip install dill
!pip install flair
!pip install nltk
!pip install spacy
!python -m spacy download en
!python -m spacy download de
!python -m spacy download pt

✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')
✔ Linking successful
/opt/venv/lib/python3.7/site-packages/en_core_web_sm -->
/opt/venv/lib/python3.7/site-packages/spacy/data/en
You can now load the model via spacy.load('en')
✔ Download and installation successful
You can now load the model via spacy.load('de_core_news_sm')
✔ Linking successful
/opt/venv/lib/python3.7/site-packages/de_core_news_sm -->
/opt/venv/lib/python3.7/site-packages/spacy/data/de
You can now load the model via spacy.load('de')
✔ Download and installation successful
You can now load the model via spacy.load('pt_core_news_sm')
✔ Linking successful
/opt/venv/lib/python3.7/site-packages/pt_core_news_sm -->
/opt/venv/lib/python3.7/site-packages/spacy/data/pt
You can now load the model via spacy.load('pt')


In [ ]:
from globalfn.annotations import all_annotations, annotation
from globalfn.alignments import all_alignments

import pickle
from pathlib import Path
import collections
import csv
import spacy

from flair.data import Sentence
from flair.embeddings import TransformerWordEmbeddings
from flair.models import SequenceTagger

import nltk
nltk.download('framenet_v17')
from nltk.corpus import framenet as fn

import scipy

[nltk_data] Downloading package framenet_v17 to
[nltk_data]     /home/jovyan/nltk_data...
[nltk_data]   Unzipping corpora/framenet_v17.zip.


In [ ]:
# Embed the n-gram of the sentence with multilingual BERT embeddings.
n_gram_size = 1
mbert = TransformerWordEmbeddings('bert-base-multilingual-cased')
def n_gram_embedding(sent, embedding_model, n=n_gram_size):
    """
    input: a sentence
    output: {send_ID: [(word or n-gram tokens, embedding), ...]}
    """
    def combined_n_gram(n, res):
        new_res = []
        for i in range(len(res) - n + 1):
            word, embedding = res[i]
            for j in range(i + 1, i + n):
                word += " " + res[j][0]
                embedding.add_(res[j][1])
            new_res.append((word, embedding/n))
        return new_res

    res = []
    sent = Sentence(sent, use_tokenizer=True)
    embedding_model.embed(sent)
    for w in sent:
        res.append((w.text, w.embedding.to('cpu')))

    return combined_n_gram(n, res)

def embed_globalfn_sentences(lang):
    # input: {sent_ID: [annotation_1, annotation_2...]}
    # output: {sent_ID: [(word1, embed1), (word2, embed2), ...]} 
    # only one embedding for the entire sentence

    # ID_to_anno_unigram_embeddings_result = {}
    # for key, val in all_annotations(lang).items():
    #     for anno in val:
    #         res = n_gram_embedding(anno.text, embedding_model=mbert, n=1)
    #         ID_to_anno_unigram_embeddings_result[key] = res
    #         break
    # pickle.dump(ID_to_anno_unigram_embeddings_result, open(f'saved/embeddings/{lang}_sent_to_mbert_unigram.pkl', 'wb'))

    # ID_to_anno_bigram_embeddings_result = {}
    # for key, val in all_annotations(lang).items():
    #     for anno in val:
    #         res = n_gram_embedding(anno.text, embedding_model=mbert, n=2)
    #         ID_to_anno_bigram_embeddings_result[key] = res
    #         break
    # pickle.dump(ID_to_anno_bigram_embeddings_result, open(f'saved/embeddings/{lang}_sent_to_mbert_bigram.pkl', 'wb'))

    ID_to_anno_bigram_embeddings_result = {}
    for key, val in all_annotations(lang).items():
        for anno in val:
            res = n_gram_embedding(anno.text, embedding_model=mbert, n=3)
            ID_to_anno_bigram_embeddings_result[key] = res
            break
    pickle.dump(ID_to_anno_bigram_embeddings_result, open(f'saved/embeddings/{lang}_sent_to_mbert_trigram.pkl', 'wb'))
    return

KeyboardInterrupt: 

In [ ]:
# embed_globalfn_sentences('en')
# embed_globalfn_sentences('de')
# embed_globalfn_sentences('pt')

/opt/venv/lib/python3.7/site-packages/torch/storage.py:34: FutureWarning: pickle support for Storage will be removed in 1.5. Use `torch.save` instead
  warnings.warn("pickle support for Storage will be removed in 1.5. Use `torch.save` instead", FutureWarning)


### Modification 1 (closest n-gram)

In [ ]:
source_sent_to_mbert_ngram = pickle.load(open(f'saved/embeddings/en_sent_to_mbert_bigram.pkl', 'rb'))
target_sent_to_mbert_ngram = pickle.load(open(f'saved/embeddings/pt_sent_to_mbert_bigram.pkl', 'rb'))

def map_sent_to_LU_embeddings(lang, embedding_pkl_file):
    """
    input: 
        - language
        - embedding_pkl_file: {send_ID: [(word or n-gram tokens, embedding), ...]}
    output: {sent_ID: [(LU1 (surface form), embedding1), ...]}
    """
    sent_to_embeddings = pickle.load(open(embedding_pkl_file, 'rb'))
    sent_to_LU_embeddings = collections.defaultdict(list)
    for sent_ID, annos in all_annotations(lang).items():
        for anno in annos:
            sent = Sentence(anno.text, use_tokenizer=True)
            token_start_positions = [token.start_position for token in sent]
            token_end_positions = [token.start_position + len(token.text) - 1 for token in sent]
            token_idxs = [token.idx - 1 for token in sent]
            # get start and end index for the LU
            for start, end, _ in anno.lu_idx:
                if start not in token_start_positions:
                    # LU index is not right
                    # print(sent_ID, start, end, anno.text[start:end+1], f'"{anno.text}"', token_start_positions, )
                    ...
                
                elif end not in token_end_positions:
                    start_idx = token_start_positions.index(start)
                    word, embedding = sent_to_embeddings[sent_ID][start_idx]
                    sent_to_LU_embeddings[sent_ID].append((word, embedding))

                    # print(start, end, anno.text[start:end+1])
                    # print(' '.join([f"{anno.text}"[token_start_positions[i]: token_end_positions[i] + 1] for i in range(len(token_start_positions))]))
                    # print(f'"{anno.text}"')
                    # raise AssertionError
                else:
                    start_idx = token_start_positions.index(start)
                    end_idx = token_end_positions.index(end)

                    idx = start_idx
                    word, embedding = sent_to_embeddings[sent_ID][idx]
                    while idx != end_idx:
                        idx += 1
                        next_word, next_embedding = sent_to_embeddings[sent_ID][idx]
                        embedding.add_(next_embedding)
                        word += " " + next_word
                    sent_to_LU_embeddings[sent_ID].append((word, embedding))
    return sent_to_LU_embeddings

# sent_to_LU_embeddings = map_sent_to_LU_embeddings('en', 'saved/embeddings/en_sent_to_mbert_unigram.pkl') 

In [ ]:
def target_identification(source_lang, target_lang, ngram):
    """
    output: 
        - {(source_sent_ID, target_sent_ID, source_LU, source_embedding): set[(potential LU, embedding, start_pos), (...)]}
    """
    source_sent_to_LU_embeddings = map_sent_to_LU_embeddings(source_lang, 
                                                             f'saved/embeddings/{source_lang}_sent_to_mbert_unigram.pkl') 
    target_sent_to_LUs = collections.defaultdict(set)  # {ID: [(potential LU, embedding), (...)]}
    ID_to_anno_bigram_embeddings_result = pickle.load(open(f"saved/embeddings/{target_lang}_sent_to_mbert_{ngram}.pkl", 'rb'))

    tmp = all_alignments(f'{source_lang}-{target_lang}')
    if tmp is None:
        tmp = all_alignments(f'{target_lang}-{source_lang}')[1]  # reverse alignments
    else:
        tmp = all_alignments(f'{target_lang}-{source_lang}')[0]


    for source, target in tmp.items():
        if type(source) is int:
            # for each annotated source sentence ID 
            for source_LU, source_embedding in source_sent_to_LU_embeddings[source]:
                for target_sent_ID in target:
                    # get best potential LU for target_sent_ID (based on cosine similarity)
                    if target_sent_ID in ID_to_anno_bigram_embeddings_result and ID_to_anno_bigram_embeddings_result[target_sent_ID]:
                        target_ngram_embeddings = ID_to_anno_bigram_embeddings_result[target_sent_ID]
                        
                        word, embedding = "", None
                        min_sim = float('inf')
                        start_pos = -1
                        sent = Sentence(annotation(target_sent_ID)[0].text, use_tokenizer=True)
                        for i, tmp in enumerate(target_ngram_embeddings):
                            target_LU, target_ngram_embedding = tmp
                            sim = scipy.spatial.distance.cosine(source_embedding.numpy(), target_ngram_embedding.numpy())
                            if sim < min_sim:
                                word, embedding = target_LU, target_ngram_embedding
                                min_sim = sim
                                start_pos = sent[i].start_pos
                        assert embedding is not None and word
                        target_sent_to_LUs[(source, target_sent_ID, source_LU, source_embedding)].add((word, embedding, start_pos))
                    else:
                        ...
    pickle.dump(target_sent_to_LUs, open(f"saved/results/modification_1/{source_lang}_{target_lang}_{ngram}_ID_to_LUs.pkl", 'wb'))
    return target_sent_to_LUs
        

In [ ]:
# print(all_alignments(f'en-pt'))

In [ ]:
# target_identification('en','de', 'unigram')
# target_identification('en','de', 'bigram')
# target_identification('en','de', 'trigram')
# target_identification('en','pt', 'unigram')
# target_identification('en','pt', 'bigram')
# target_identification('en','pt', 'trigram')
target_identification('pt','en', 'unigram')
target_identification('pt','en', 'bigram')
target_identification('pt','en', 'trigram')
# target_identification('pt','de', 'unigram')
# target_identification('pt','de', 'bigram')
# target_identification('pt','de', 'trigram')

TypeError: 'NoneType' object is not subscriptable

In [ ]:
def combined_target_identification(source_lang, target_lang):
    """
    output: 
        - {(source_sent_ID, target_sent_ID, source_LU, source_embedding): (potential LU, embedding)}
    """
    results = collections.defaultdict(set)

    # combine the results from unigram, bigram, ... target_identification
    pathlist = Path("saved/results/modification_1").glob(f'{source_lang}_{target_lang}_*.pkl')
    for path in pathlist:
        ngram_ID_to_LUs = pickle.load(open(path, 'rb'))
        for key, val in ngram_ID_to_LUs.items():
            for pot_LU, embedding in val:
                results[key].add((pot_LU, embedding))

    combined_results = dict()
    
    for key, val in results.items():
        # key = (source_sent_ID, target_sent_ID, source_LU, source_embedding)
        # val = (potential LU, embedding)

        source_embedding = key[-1]
        final_LU, final_embedding, min_sim = "", None, float('inf')
        for target_LU, target_ngram_embedding in val:
            sim = scipy.spatial.distance.cosine(source_embedding.numpy(), target_ngram_embedding.numpy())
            if sim < min_sim:
                final_LU, final_embedding = target_LU, target_ngram_embedding
                min_sim = sim
        
        combined_results[key] = (final_LU, final_embedding)
    
    pickle.dump(combined_results, open(f"saved/results/modification_1/{source_lang}_{target_lang}_3_ID_to_LUs.pkl", 'wb'))
    return combined_results

In [ ]:
combined_target_identification('en', 'pt')
combined_target_identification('en', 'de')

{(1010,
  1277,
  'great',
  tensor([-0.2523,  0.3761,  0.1597,  ...,  1.3981,  1.0167,  0.4188])): ('großartig ,',
  tensor([-0.4072, -0.5083, -0.1111,  ...,  0.7826,  0.6192,  0.4672])),
 (1011,
  1278,
  'blown',
  tensor([-0.0735, -0.9338, -0.0724,  ...,  0.3561, -0.1237,  0.5176])): ('umgehauen .',
  tensor([-0.3929, -0.6843,  0.3647,  ...,  0.8974,  1.2477,  0.0338])),
 (1011,
  1278,
  'thing',
  tensor([-0.5206, -0.5303, -0.2309,  ...,  1.1143,  0.1765,  0.9568])): ('Sache hier',
  tensor([-0.2105, -0.5874,  0.3833,  ...,  0.6838,  0.3947,  0.2352])),
 (1011,
  1278,
  'whole',
  tensor([-0.2384, -0.7315, -0.2455,  ...,  0.9658,  0.3931,  2.1352])): ('ganze Sache',
  tensor([-0.1582, -0.7760,  0.4221,  ...,  0.3528,  0.4560,  0.5730])),
 (1012,
  1279,
  'leaving',
  tensor([-0.3542, -0.8160,  0.1723,  ...,  1.3257,  0.1010,  0.3451])): ('jetzt .',
  tensor([-0.0495, -0.1719,  0.2700,  ...,  1.0122,  0.8182, -0.2491])),
 (1013,
  1280,
  'three',
  tensor([-0.2961,  0.1849,  1.

### Basic (Based on Any-Language-Parser)

In [ ]:
# tag each word token with POS
tagger = SequenceTagger.load('pos-multi')

def tag_pos(sent, tagger):
    sent = Sentence(sent, use_tokenizer=True)
    tagger.predict(sent)
    pos_result = list()
    for token in sent.tokens:
        # pos_result.append((token.text, token.annotation_layers))
        pos_result.append((token.text, token.start_pos, token.get_labels('upos')[0].value))
    return pos_result

def tag_pos_globalfn_sentences(lang):
    # input: {sent_ID: [annotation_1, annotation_2...]}
    # output: {sent_ID: [(word1, token1.start_pos, pos1), (word2, token2.start_pos, pos2), ...]} 
    # only one tagging for the entire sentence

    ID_to_anno_pos_result = {}
    for key, val in all_annotations(lang).items():
        for anno in val:
            res = tag_pos(anno.text, tagger)
            ID_to_anno_pos_result[key] = res
            break
    pickle.dump(ID_to_anno_pos_result, open(f'saved/pos/{lang}_sent_to_pos.pkl', 'wb'))
    return 

2020-06-08 02:10:29,161 https://s3.eu-central-1.amazonaws.com/alan-nlp/resources/models-v0.4/release-dodekapos-512-l2-multi/pos-multi-v0.1.pt not found in cache, downloading to /tmp/tmp7o4uq79w
100%|██████████| 314055714/314055714 [00:15<00:00, 20205822.00B/s]2020-06-08 02:10:45,421 copying /tmp/tmp7o4uq79w to cache at /home/jovyan/.flair/models/pos-multi-v0.1.pt

2020-06-08 02:10:45,782 removing temp file /tmp/tmp7o4uq79w
2020-06-08 02:10:45,813 loading file /home/jovyan/.flair/models/pos-multi-v0.1.pt


In [ ]:
# # tag each sentence
# tag_pos_globalfn_sentences('en')
# tag_pos_globalfn_sentences('de')
# tag_pos_globalfn_sentences('pt')

In [ ]:
# lemmatize the sentences
def lemmatize_globalfn_sentences(lang):
    # input: {sent_ID: [annotation_1, annotation_2...]}
    # output: {sent_ID: [lemma1, lemma2, ...]} 
    # only one tagging for the entire sentence
    nlp = spacy.load(lang)
    
    ID_to_anno_lemmas_result = {}
    for key, val in all_annotations(lang).items():
        for anno in val:
            doc = nlp(Sentence(anno.text, use_tokenizer=True).to_tokenized_string())
            ID_to_anno_lemmas_result[key] = [token.lemma_ for token in doc]
            break
    pickle.dump(ID_to_anno_lemmas_result, open(f'saved/pos/{lang}_sent_lemmas.pkl', 'wb'))
    return 

In [ ]:
# lemmatize_globalfn_sentences('en')
# lemmatize_globalfn_sentences('pt')
# lemmatize_globalfn_sentences('de')

In [ ]:
# identify lemmas tagged with the most common POS tags
def identify_lemmas_with_most_common_pos(lang):
    """
    input: 
        - sent_to_lemmas: {sent_ID: [lemma1, lemma2, ...]} 
        - sent_to_pos: {sent_ID: [(word1, token1.start_pos, pos1), (word2, token2.start_pos, pos2), ...]} 
    output: {sent_ID: [(word1, lemma1, token1.start_pos, pos1),  ...]} 
    """
    sent_to_pos = pickle.load(open(f'saved/pos/{lang}_sent_to_pos.pkl', 'rb'))
    sent_to_lemmas = pickle.load(open(f'saved/pos/{lang}_sent_lemmas.pkl', 'rb'))
    count_pos_tag = collections.Counter()

    for key, val in sent_to_pos.items():
        for _, _, pos_tag in val:
            count_pos_tag[pos_tag] += 1

    most_common_pos = set([most_common_pos for most_common_pos, _ in count_pos_tag.most_common()[:8]]) - set(['PUNCT'])

    spacy_nlp = spacy.load(lang)
    ID_to_words_common_pos = collections.defaultdict(list)
    for key, val in sent_to_pos.items():
        for i in range(len(val)):
            word, start_pos, pos_tag = val[i]
            if pos_tag in most_common_pos:
                # if the lemmatized sentence is of the same length of the tokenized POS-tagged sentence 
                if len(val) == len(sent_to_lemmas[key]):
                    lemma = sent_to_lemmas[key][i]
                    ID_to_words_common_pos[key].append((word, lemma, start_pos, pos_tag))
                else:
                    lemma = [token.lemma_ for token in spacy_nlp(word)][0]
                    ID_to_words_common_pos[key].append((word, lemma, start_pos, pos_tag))

    pickle.dump(ID_to_words_common_pos, open(f'tmps/{lang}_lemmas_with_most_common_pos.pkl', 'wb'))


In [ ]:
identify_lemmas_with_most_common_pos('en')
identify_lemmas_with_most_common_pos('de')
identify_lemmas_with_most_common_pos('pt')

defaultdict(<class 'list'>, {1010: [('It', '-PRON-', 0, 'PRON'), ("'s", 'be', 2, 'AUX'), ('been', 'be', 5, 'AUX'), ('has', 'have', 17, 'AUX'), ('it', '-PRON-', 24, 'PRON')], 1011: [('I', '-PRON-', 0, 'PRON'), ("'ve", "'", 1, 'AUX'), ('been', 'be', 5, 'AUX'), ('blown', 'blown', 10, 'VERB'), ('away', 'away', 16, 'ADV'), ('by', 'by', 21, 'ADP'), ('the', 'the', 24, 'DET'), ('thing', 'thing', 34, 'NOUN')], 1012: [('In', 'in', 0, 'ADP'), ('fact', 'fact', 3, 'NOUN'), ('I', '-PRON-', 9, 'PRON'), ("'m", "'", 10, 'AUX'), ('leaving', 'leave', 13, 'VERB')], 1013: [('There', 'there', 0, 'PRON'), ('have', 'have', 6, 'AUX'), ('been', 'be', 11, 'VERB'), ('themes', 'theme', 22, 'NOUN'), ('running', 'run', 29, 'VERB'), ('through', 'through', 37, 'ADP'), ('the', 'the', 45, 'DET'), ('conference', 'conference', 49, 'NOUN'), ('which', 'which', 60, 'PRON'), ('are', 'be', 66, 'AUX'), ('what', 'what', 82, 'PRON'), ('I', '-PRON-', 87, 'PRON'), ('want', 'want', 89, 'VERB'), ('talk', 'talk', 97, 'VERB'), ('about'

In [ ]:
def get_translated_synsets(lang):
    """
    input: {sent_ID: [(word1, lemma1, token1.start_pos, pos1),  ...]} 
    output: {sent_ID: [(word1, lemma1, token1.start_pos, pos1, [en_synset1, en_synset2, ...]), ...]}
    """
    if lang == 'de':
        wikt_lang = 'deu'
    elif lang == 'pt':
        wikt_lang = 'por'
    elif lang == 'en':
        wikt_lang = 'eng'
    else:
        assert False

    lemma_to_wncode = collections.defaultdict(list)
    with open(f"/datasets/extended_omw/data/wikt/wn-wikt-{wikt_lang}.tab", 'r+') as rf:
        next(rf)
        for line in rf:
            if len(line.strip().split('\t')) < 3:
                continue
            wncode, _, lemma = line.strip().split('\t')
            lemma_to_wncode[lemma.lower()].append(wncode)

    with open(f"/datasets/extended_omw/data/cldr/wn-cldr-{wikt_lang}.tab", 'r+') as rf:
        next(rf)
        for line in rf:
            wncode, _, lemma = line.strip().split('\t')
            lemma_to_wncode[lemma.lower()].append(wncode)

    wncode_to_wn_word = {}
    with open ('/datasets/extended_omw/data/wordnetwiktionaryalignments-2013-02-19.tsv', 'r+') as rf:
        next(rf)
        for line in rf:
            wncode, _, wnword, *_ = line.strip().split('\t')
            wncode_to_wn_word[wncode] = list(wnword.split(','))

    ID_to_words_common_pos = pickle.load(open(f'/home/jovyan/work/tmps/{lang}_lemmas_with_most_common_pos.pkl', 'rb'))
    ID_to_translated_wnsynsets = collections.defaultdict(list)
    for key, val in ID_to_words_common_pos.items():
        for word, lemma, start_pos, pos in val:
            # account for case-sensitivity
            if lemma.lower() in lemma_to_wncode:
                for wncode in lemma_to_wncode[lemma.lower()]:
                    ID_to_translated_wnsynsets[key].append((word, lemma, start_pos, pos, wncode_to_wn_word[wncode]))
    print(ID_to_translated_wnsynsets)
    pickle.dump(ID_to_translated_wnsynsets, open(f'tmps/{lang}_ID_to_translated_wnsynsets.pkl', 'wb'))

In [ ]:
# get_translated_synsets('de')
# get_translated_synsets('pt')
# get_translated_synsets('en')

In [ ]:
def target_identification(lang):
    """
    input: {sent_ID: [(word1, lemma1, token1.start_pos, pos1, [en_synset1, en_synset2, ...]), ...]}
    output: ID_to_LUs {ID: (word, lemma, start_pos, pos): {framenet_lus.ID}}
    """
    ID_to_translated_wnsynsets = pickle.load(open(f'tmps/{lang}_ID_to_translated_wnsynsets.pkl', 'rb'))

    ID_to_LUs = collections.defaultdict(dict)  #ID -> (word, lemma, start_pos, pos) -> {framenet_lus.ID}
    for sent_ID, val in ID_to_translated_wnsynsets.items():
        framenet_lus = collections.defaultdict(set)
        for word, lemma, start_pos, pos, wnsynsets in val:
            for synset in wnsynsets:
                for lu in fn.lus(synset):
                    framenet_lus[(word, lemma, start_pos, pos)].add(lu.ID)
        ID_to_LUs[sent_ID] = framenet_lus
    pickle.dump(ID_to_LUs, open(f'saved/results/{lang}_ID_to_LUs.pkl', 'wb'))

In [ ]:
# target_identification('de')
# target_identification('pt')
target_identification('en')

In [ ]:
pickle.load(open(f'saved/results/en_ID_to_LUs.pkl', 'rb'))

defaultdict(dict,
            {1010: defaultdict(set,
                         {("'s", 'be', 2, 'AUX'): {67,
                           130,
                           150,
                           210,
                           211,
                           534,
                           550,
                           551,
                           570,
                           640,
                           641,
                           789,
                           790,
                           1055,
                           1085,
                           1162,
                           1189,
                           1344,
                           1569,
                           1628,
                           1744,
                           1812,
                           2000,
                           2002,
                           2037,
                           2062,
                           2070,
                           2071,
            